In [2]:
import numpy as np
import pylab as plt

import networkx as nx
import random as rand


# Policy gradient methods

In the previous methods we construct the policy solving a fixed point problem on the **Q-function**. This function allows to evaluate the action policy choose by the policy. We speak about **purely critic algorithm**.

In the following we will introduce some algorithms where we compute directly the policy **minimizing a functionnal**. We speak about:
- **purely actor** if the algorithm compute only the **policy**,
- **actor-critic** if the algorithm compute the **policy** and the **Q-function**,
- **purely critic** if the algorithm compute only the **Value or Q-function**. Exemple: **DQN** method.

These algorithms are given only for policy/Q-function described by **parameters (ANN for example)** for the continuous state space framework.

We consider a parametrized **stochastic policy**: $\pi_{\theta}(\mathbf{a}\mid \mathbf{s})$ with $\theta$ the parameters and $\gamma=1$

In the Q-learning/Deep Q learning the idea was to compute/approximate a global optimum which maximize a **discounted return** defined by a fixed point problem (Bellmann optimality equation).

Since we have a parametrized policy this policy is **differentiable** function. Consequently we can maximize/minimize a functionnal of this policy using **gradient methods**.

The aim is to **maximize**:

$$
\mathcal{J}(\theta) = \mathbb{E}[\mathbf{G}_t \mid \pi_{\theta}] = \int_S p_0(\mathbf{s})V_{\pi_{\theta}}(\mathbf{s})d \mathbf{s}
$$

with $p(.)$ the distribution of the initial state.

**Lemma**:

*The functionnal can be rewrite as*:

$$
\mathcal{J}(\theta)=\int_s \rho^{\pi_{\theta}}(\mathbf{s})\left(\sum_\mathbf{a}\pi_{\theta}(\mathbf{a}\mid \mathbf{s})r(\mathbf{a}, \mathbf{s}) \right) d\mathbf{s} 
$$

with the **discounted distribution state** 

$$
\rho^{\pi}(\mathbf{s})= \int_{S}\sum_{t=0}^{\infty}\gamma^t p(\mathbf{s}_0)P(\mathbf{s}_0\rightarrow \mathbf{s},t,\pi_{\theta}) d\mathbf{s}_0
$$

*proof*

$$
\mathcal{J}(\theta) = \mathbb{E}\left[\sum_{t=0}^{\infty} \gamma^t\mathbf{r}_t \mid \pi_{\theta}\right]= \sum_{t=0}^{\infty} \gamma^t\mathbb{E}\left[ \mathbf{r}_t \mid \pi_{\theta}\right]
$$

$$
\sum_{t=0}^{\infty} \gamma^t\mathbb{E}\left[ \mathbf{r}_t \mid \pi_{\theta}\right] = \sum_{t=0}^{\infty}\gamma^t\int_S d(\mathbf{s},t)\left(\sum_{\mathbf{a}} \pi(\mathbf{a} \mid \mathbf{s})\mathbf{r}(\mathbf{a},\mathbf{a})\right)d \mathbf{s}
$$

with a $d$ a distribution of the state at the time $t$. This distribution can be written as

$$
d(\mathbf{s},t)=\int_{S}p(\mathbf{s}_0)P(\mathbf{s}_0\rightarrow \mathbf{s},t,\pi_{\theta}) d\mathbf{s}_0
$$

with $P$ a probability to arrive at the state $\mathbf{s}$ with start point $\mathbf{s}_0$ following the policy $\pi$ at the time $t$ .We use that

$$
\sum_{t=0}^{\infty} \gamma^t\mathbb{E}\left[ \mathbf{r}_t \mid \pi_{\theta}\right] = \sum_{t=0}^{\infty}\gamma^t\int_S \int_{S}p(\mathbf{s}_0)P(\mathbf{s}_0\rightarrow \mathbf{s},t,\pi_{\theta}) d\mathbf{s}_0\left(\sum_{\mathbf{a}} \pi(\mathbf{a} \mid \mathbf{s})\mathbf{r}(\mathbf{a},\mathbf{a})\right)d \mathbf{s}
$$

$$
\sum_{t=0}^{\infty} \gamma^t\mathbb{E}\left[ \mathbf{r}_t \mid \pi_{\theta}\right] = \int_S \int_{S}\sum_{t=0}^{\infty}\gamma^t p(\mathbf{s}_0)P(\mathbf{s}_0\rightarrow \mathbf{s},t,\pi_{\theta}) d\mathbf{s}_0\left(\sum_{\mathbf{a}} \pi(\mathbf{a} \mid \mathbf{s})\mathbf{r}(\mathbf{s},\mathbf{a})\right)d \mathbf{s}
$$

We define the discouted distribution state $\rho^{\pi}(\mathbf{s})$ to conclude the proof.

*end proof*

References:
- (1 )https://hal.archives-ouvertes.fr/hal-00764281

**Theorem (Gradient policy)**:

*The gradient of the previous functional is given by*

$$
\nabla \mathcal{J}(\theta) = \int_S \rho^{\pi}(\mathbf{s}) \left(\sum_{\mathbf{a}} \nabla_{\theta}\pi_{\theta}(\mathbf{a} \mid \mathbf{s})Q^{\pi_{\theta}}(\mathbf{s},\mathbf{a})\right)d \mathbf{s}
$$
$$
= \mathbb{E}_{\pi_{\theta}}\left[\sum_{\mathbf{a}}Q^{\pi_{\theta}}(\mathbf{s},\mathbf{a})\nabla_{\theta} \pi_{\theta}(\mathbf{a}\mid \mathbf{s})\right]
$$

with $\mathbb{E}_{\pi_{\theta}}$ the esperance where the state are given by the distribution $\rho^{\pi_{\theta}}$ and the action by the policy.
 

*proof*

We take


$$
\mathcal{J}(\theta) = \int_S p_0(\mathbf{s}_0)V_{\pi_{\theta}}(\mathbf{s}_0)d \mathbf{s}_0
$$
$$
\mathcal{J}(\theta) = \int_S p_0(\mathbf{s}_0)\left(\sum_a \pi_{\theta}(\mathbf{a}_0\mid \mathbf{s}_0)Q_{\pi_{\theta}}(\mathbf{s}_0,\mathbf{a}_0)\right)d \mathbf{s}_0
$$

Now we compute the gradient. We have

$$
\nabla_{\theta }\mathcal{J}(\theta) = \underbrace{\int_S p_0(\mathbf{s}_0)\left(\sum_a \nabla_{\theta }\pi_{\theta}(\mathbf{a}_0\mid \mathbf{s}_0)Q_{\pi_{\theta}}(\mathbf{s}_0,\mathbf{a}_0)\right)d \mathbf{s}_0}_{A_1} + \underbrace{\int_S p_0(\mathbf{s}_0)\left(\sum_a \pi_{\theta}(\mathbf{a}_0\mid \mathbf{s}_0)\nabla_{\theta }Q_{\pi_{\theta}}(\mathbf{s}_0,\mathbf{a}_0)\right)d \mathbf{s}_0}_{A_2}
$$

Now we use Bellman:

$$
Q_{\pi_{\theta}}(\mathbf{s}_0,\mathbf{a}_0) = \mathbf{r}(\mathbf{s}_0,\mathbf{a}_0) + \gamma \int_{S}P(\mathbf{s}_1| \mathbf{s}_0,\mathbf{a}_0) V(\mathbf{s}_1) d\mathbf{s}_1
$$

We have 

$$
 A_2=\int_S p_0(\mathbf{s}_0)\left(\sum_a \pi_{\theta}(\mathbf{a}_0\mid \mathbf{s}_0)\nabla_{\theta }Q_{\pi_{\theta}}(\mathbf{s}_0,\mathbf{a}_0)\right)d \mathbf{s}_0 =  \int_S p_0(\mathbf{s}_0)\left(\sum_a \pi_{\theta}(\mathbf{a}_0\mid \mathbf{s}_0)\nabla_{\theta} \left(\mathbf{r}(\mathbf{s}_0,\mathbf{a}_0) + \gamma \int_{S}P(\mathbf{s}_1| \mathbf{s}_0,\mathbf{a}_0) V(\mathbf{s}_1) d\mathbf{s}_1 \right) \right)d \mathbf{s}_0
$$

$$
 A_2=\int_S p_0(\mathbf{s}_0)\left(\sum_a \pi_{\theta}(\mathbf{a}_0\mid \mathbf{s}_0)\nabla_{\theta }Q_{\pi_{\theta}}(\mathbf{s}_0,\mathbf{a}_0)\right)d \mathbf{s}_0 =  \int_S p_0(\mathbf{s}_0)\left(\sum_a \pi_{\theta}(\mathbf{a}_0\mid \mathbf{s}_0)\nabla_{\theta} \left( \gamma \int_{S}P(\mathbf{s}_1| \mathbf{s}_0,\mathbf{a}_0) V(\mathbf{s}_1) d\mathbf{s}_1 \right) \right)d \mathbf{s}_0
$$

since reward at one step does not depend of the policy.

$$
 A_2 = \int_S p_0(\mathbf{s}_0)\left(\sum_a \pi_{\theta}(\mathbf{a}_0\mid \mathbf{s}_0)\nabla_{\theta} \left( \gamma \int_{S}P(\mathbf{s}_1| \mathbf{s}_0,\mathbf{a}_0) \nabla_{\theta}V(\mathbf{s}_1) d\mathbf{s}_1 \right) \right)d \mathbf{s}_0
$$

Now we use fubini theorem to obtain

$$
A_2 =  \int_S \left(\int_S \gamma p_0(\mathbf{s}_0)\left(\sum_a \pi_{\theta}(\mathbf{a}_0\mid \mathbf{s}_0) P(\mathbf{s}_1| \mathbf{s}_0,\mathbf{a}_0)\right) d\mathbf{s}_0 \right) \nabla_{\theta} V_{\pi_{\theta}}(\mathbf{s}_1) d \mathbf{s}_1
$$

We define $P(\mathbf{s}_0\rightarrow \mathbf{s}_1,1,\pi_{\theta})=\sum_a \pi_{\theta}(\mathbf{a}_0\mid \mathbf{s}_0) P(\mathbf{s}_1| \mathbf{s}_0,\mathbf{a}_0)$ 

We obtain the 

$$
A_2 = \int_S \left(\int_S \gamma p_0(\mathbf{s}_0) P(\mathbf{s}_0\rightarrow \mathbf{s}_1,1,\pi_{\theta}) d\mathbf{s}_0 \right) \nabla_{\theta} V_{\pi_{\theta}}(\mathbf{s}_1) d \mathbf{s}_1
$$

Now we use that $V_{\pi_{\theta}}(\mathbf{s}_1)=\sum_a \pi_{\theta}(\mathbf{a}_1\mid \mathbf{s}_1) Q(\mathbf{s}_1, \mathbf{a}_1)$ to obtain

$$
A_2 = \int_S \left(\int_S \gamma p_0(\mathbf{s}_0) P(\mathbf{s}_0\rightarrow \mathbf{s}_1,1,\pi_{\theta}) d\mathbf{s}_0 \right) \nabla_{\theta} \left(\sum_a \pi_{\theta}(\mathbf{a}\mid \mathbf{s}_1) Q(\mathbf{s}_1, \mathbf{a})\right) d \mathbf{s}_1
$$

Now we consider the total gradient:

$$
\nabla_{\theta }\mathcal{J}(\theta) = \int_S p_0(\mathbf{s}_0)\left(\sum_a \nabla_{\theta }\pi_{\theta}(\mathbf{a}_0\mid \mathbf{s}_0)Q_{\pi_{\theta}}(\mathbf{s}_0,\mathbf{a}_0)\right)d \mathbf{s}_0 +\int_S \left(\int_S \gamma p_0(\mathbf{s}_0) P(\mathbf{s}_0\rightarrow \mathbf{s}_1,1,\pi_{\theta}) d\mathbf{s}_0 \right) \nabla_{\theta} \left(\sum_a \pi_{\theta}(\mathbf{a}\mid \mathbf{s}_1) Q(\mathbf{s}_1, \mathbf{a})\right) d \mathbf{s}_1
$$

To compute the term $\nabla_{\theta} \left(\sum_a \pi_{\theta}(\mathbf{a}\mid \mathbf{s}_1) Q(\mathbf{s}_1, \mathbf{a})\right)$ we will use the same computation as before:
- gradient of product
- for the term with the gradient of $Q_1$ we use Bellman
- we use Fubini and the Probability transition between $\mathbf{s}_1$ and $\mathbf{s}_2$

Finally using this iterative computation along a time trajectory we obtain that

$$
\nabla_{\theta }\mathcal{J}(\theta) = \sum_{t}^{\infty}\int_S\left(\int_S\gamma^t p_0(\mathbf{s}_0)P(\mathbf{s}_0 \rightarrow \mathbf{s},t,\pi_{\theta}) d\mathbf{s}_0\right)\left(\sum_{\mathbf{a}} \nabla_{\theta }\pi_{\theta}(\mathbf{a}\mid \mathbf{s})Q_{\pi_{\theta}}(\mathbf{s},\mathbf{a})\right)d \mathbf{s}
$$

$$
\nabla_{\theta }\mathcal{J}(\theta) = \int_S\left(\int_S\sum_{t}^{\infty}\gamma^t p_0(\mathbf{s}_0)P(\mathbf{s}_0 \rightarrow \mathbf{s},t,\pi_{\theta}) d\mathbf{s}_0\right)\left(\sum_{\mathbf{a}} \nabla_{\theta }\pi_{\theta}(\mathbf{a}\mid \mathbf{s})Q_{\pi_{\theta}}(\mathbf{s},\mathbf{a})\right)d \mathbf{s}
$$

since the last term $\left(\sum_{\mathbf{a}} \nabla_{\theta }\pi_{\theta}(\mathbf{a}\mid \mathbf{s})Q_{\pi_{\theta}}(\mathbf{s},\mathbf{a})\right)$ doest not depend of the time. So we have

$$
\nabla_{\theta }\mathcal{J}(\theta) = \int_S\rho^{\pi_{\theta}}(\mathbf{s})\left(\sum_{\mathbf{a}} \nabla_{\theta }\pi_{\theta}(\mathbf{a}\mid \mathbf{s})Q_{\pi_{\theta}}(\mathbf{s},\mathbf{a})\right)d \mathbf{s}
$$

*end proof*


 
**Corollary**:

*the gradient can be compute by*:

$$
\nabla \mathcal{J}(\theta) = \mathbb{E}_{\pi^{\theta}}\left[Q^{\pi_{\theta}}(\mathbf{s},\mathbf{a})\nabla_{\theta} \operatorname{ln} \pi_{\theta}(\mathbf{a}\mid \mathbf{s})\right]
$$

*proof*
 We consider the last equation of the theorem
 
$$
\nabla \mathcal{J}(\theta)  =\mathbb{E}_{\pi_{\theta}}\left[\sum_{\mathbf{a}}Q^{\pi_{\theta}}(\mathbf{s},\mathbf{a})\nabla_{\theta} \pi_{\theta}(\mathbf{a}\mid \mathbf{s})\right]
$$

$$
\nabla \mathcal{J}(\theta)  =\mathbb{E}_{\pi_{\theta}}\left[\sum_{\mathbf{a}}\pi_{\theta}(\mathbf{a}\mid \mathbf{s})Q^{\pi_{\theta}}(\mathbf{s},\mathbf{a})\frac{\nabla_{\theta} \pi_{\theta}(\mathbf{a}\mid \mathbf{s})}{\pi_{\theta}(\mathbf{a}\mid \mathbf{s})}\right]
$$

Since we follow the policy the action $\mathbf{a}$ is given by the policy $\pi_{\theta}$. By definition $\pi(\mathbf{a}^{'}\mid \mathbf{s})=1$ and $\pi(\mathbf{a}^{'}\mid \mathbf{s})=0$ with $\mathbf{a} \neq \mathbf{a}$. So we have

$$
\nabla \mathcal{J}(\theta)  =\mathbb{E}_{\pi_{\theta}}\left[Q^{\pi_{\theta}}(\mathbf{s},\mathbf{a})\frac{\nabla_{\theta} \pi_{\theta}(\mathbf{a}\mid \mathbf{s})}{\pi_{\theta}(\mathbf{a}\mid \mathbf{s})}\right]
$$

which is equal, using the log derivative, to the result.

*end proof*

**Remark**:

In the following we will estimate this gradient and use a grandient method to update the weights of the parameter policy. 

The stochastic policy is a function which gives the **probability of each action** for one state which will maximize our criterium. We see that it is a **classification problem**. If we approximate the policy by a **ANN** it will be classifying ANN.

We remark that the term $\operatorname{ln} \pi_{\theta}(\mathbf{a}\mid \mathbf{s})$ present in the gradient correspond the **cross entropy loss** use in classification.

So At the ANN part we will **solve a classfication problem on the action**


## Reinforce method



The **REINFORCE** method is the most basic algorithm of **policy gradient**. It based on a Monte-Carlo approach.

This method is a **purely actor** method.

References: 

- https://lilianweng.github.io/lil-log/2018/04/08/policy-gradient-algorithms.html#off-policy-policy-gradient

- https://medium.com/@thechrisyoon/deriving-policy-gradients-and-implementing-reinforce-f887949bd63 (very important for coding)

- https://medium.com/@jonathan_hui/rl-policy-gradients-explained-9b13b688b146

- https://lilianweng.github.io/lil-log/2018/04/08/policy-gradient-algorithms.html#reinforce

- https://medium.com/@amitpatel.gt/policy-gradients-1edbbbc8de6b (NEW, we learn with more that one episode)

We consider the gradient 

$$
\nabla \mathcal{J}(\theta)  =\mathbb{E}_{\pi_{\theta}}\left[Q^{\pi_{\theta}}(\mathbf{s},\mathbf{a})\nabla_{\theta} \operatorname{ln} \pi_{\theta}(\mathbf{a}\mid \mathbf{s})\right]
$$

Since $Q^{\pi_{\theta}}(\mathbf{s},\mathbf{a}) =\mathbb{E}^{\pi_{\theta}}\left[\mathbf{G}_t\mid \mathbf{s}_t=\mathbf{s},\mathbf{a}_t=\mathbf{a}\right]$ we can use as **unbiased sample** of $Q^{\pi_{\theta}}(\mathbf{s},\mathbf{a})$ a discounted reward $\mathbf{G}_t$ (verify this part ?)

So we have 

$$
\nabla \mathcal{J}(\theta)  =\mathbb{E}_{\pi_{\theta}}\left[\mathbf{G}_t\nabla_{\theta} \operatorname{ln} \pi_{\theta}(\mathbf{a}\mid \mathbf{s})\right]
$$

The idea now, to compute the esperance is to use a Monte-Carlo method which use an emperical average:

$$
\nabla \mathcal{J}(\theta) \approx \frac{1}{m}\sum_{i=0}^m \left(\sum_{t=0}^T \left(\mathbf{G}_t\nabla_{\theta} \operatorname{ln} \pi_{\theta}(\mathbf{a}_t\mid \mathbf{s}_t)\right)\right)_i
$$

Since the **trajectories are generated by the policy** $\pi_{\theta}$ compute the MC method using this trajectories allows to sample the distribution $\rho^{\pi_{\theta}}$.

if we use a **Classical descent Gradient** tu update the weights $\theta$ of the ANN we obtain the following increment

$$
\theta_{k+1}=\theta_{k}+ \alpha_k \mathcal{J}(\theta)
$$

with the gradient given by the previous approximation.

For the Neural-Network level we can see as a mini-batch gradient method. 

We consider the term $$\mathbf{G}_t\nabla_{\theta} \operatorname{ln} \pi_{\theta}(\mathbf{a}_t\mid \mathbf{s}_t)$$

The **cross entropy Loss** is given for $n$ category by

$$
-\sum_i^n y_i \operatorname{log} \hat{y}_i
$$

with $\hat{y}_i$ the probability predicted by the neural network for the class $i$ and $y_i$ the reference probability for the class $i$.

If $y_{i_0}=1$ and $y_{i}=0$ for $i\neq i_0$ we have supervised learning where we known the reference category.

In this case, it is difference the probability is given by the **discounted reward**. So more the reward for one action is important, more the reference probability for this action increase.
Consequently the actor will be learn a higher probability for this action.

By definition, at the end of the learning. The action maximizing the reward will be obtain the higher probability. 

**Algorithm (REINFORCE)**:
- Initialize $\theta$ arbitrarly
- for the estimate $k< E$:
 - for all episodes $M$ of the estimate
     - choose randomly a initial state $\mathbf{s}_0$
     - compute and store a trajectory $(\mathbf{s}_0,\mathbf{a}_0,\mathbf{r}_1,\mathbf{s}_1,...,\mathbf{r}_T)$ 
     following $\pi_{\theta_k}(.\mid.)$
     - compute all the discounted reward $\mathbf{G}=(\mathbf{G}_0,...,\mathbf{G}_{T-1})$
 - update the ANN $\pi_{\theta_{k+1}}(.\mid.)$ with a **spare-cross-entropy loss** with
   - $\mathbf{y}$ as predicted values,
   - list of index action as target values,
   - $\mathbf{G}$ as sample weight of the loss.

**Remark**:
For now we have not details how the probability law $\pi_{\theta_k}(.\mid.)$ is constructed.

The idea is to construct the law seuch that: the actions with the highest preferences in each state are given the highest probabilities of being selected, for example.

For that the natural choice is the **exponential softmax distribution**:

$$
\pi(\mathbf{a}\mid \mathbf{s}) = \frac{e^{h(\mathbf{a},\mathbf{s})}}{\sum_{\mathbf{b}}e^{h(\mathbf{b},\mathbf{s})}}
$$

with $h(.,.)$ a preference function.

To obtain a result like that it is sufficient to use a **softmax activation** function at the end of your ANN.

In [2]:
class REINFORCE:

    def __init__(self, env, monitor, layer_sizes, batch_size=32, experience_size=1024, gamma= 0.95, lr=0.001):
        self.env = env
        self.monitor= monitor
        self.layer_sizes = layer_sizes
        self.batch_size = batch_size
        self.gamma = gamma
        self.lr = lr
        self.network = self._new_network()
        self.network.compile(optimizer=keras.optimizers.Adam(lr=self.lr), 
                             loss='sparse_categorical_crossentropy')

    def _new_network(self):
        X_input = tf.keras.layers.Input([len(self.env.x)])
        X = X_input
        print(">>>> size ",self.env.nactions)
        for i in self.layer_sizes:
            X = tf.keras.layers.Dense(i, activation="elu")(X)
        Y = tf.keras.layers.Dense(self.env.nactions, activation="softmax")(X)
        model = tf.keras.Model(inputs=X_input, outputs=Y)
        return model

    def exploratory_policy(self, x):
        res = np.zeros(self.env.nactions)
        res = self.network.predict(x[None,:])
        return res
    
    def _MC_generate_episode(self,T):
        episode =[]
        self.env.reset()
        self.monitor.update(self.env.t, self.env.x, 0.0)
        for t in range(T):
            x = self.env.x
            p = self.exploratory_policy(x)
            index_a = np.random.choice(self.env.nactions, p=p)
            y, r = self.env.update(index_a)
            final = self.env.is_final(y)
            self.monitor.update(self.env.t, y, r)
            episode.append((x,index_a,r))
          
        return episode

    def run(self, E=10, M=10, T=100):
        for estimate in range(E):
            Gt = []
            st = []
            at = []
            for e in range(M):
                episode = self._MC_generate_episode(T)
                for j in range(len(episode)):
                    Gloc = sum([(self.gamma**i)*sar[2] for i,sar in enumerate(episode[j:])]) ## verify the power
                    Gt.append(Gloc)
                    st.append(sar[0])
                    at.append(sar[1])
                
            ## transpose at ,??? comme Vincent    
            mean_Gt = np.mean(Gt)
            std_Gt = np.std(Gt)
            normGt = []
            normGt = (Gt-mean_Gt)/(std_Gt + 1e-7)
              
            self.network.fit(st, at,
            batch_size=len(Gt), ### a random batch in the previous one
            sample_weight=Gt, 
            epochs=1, 
            verbose=0)
                  
        if estimate % 10==0:
            self.monitor.plot()

## Actor-critic method

References:

- https://lilianweng.github.io/lil-log/2018/04/08/policy-gradient-algorithms.html#off-policy-policy-gradient

- https://towardsdatascience.com/understanding-actor-critic-methods-931b97b6df3f

We consider agains the gradient 

$$
\nabla \mathcal{J}(\theta)  =\mathbb{E}_{\pi_{\theta}}\left[Q^{\pi_{\theta}}(\mathbf{s}_t,\mathbf{a}_t)\nabla_{\theta} \operatorname{ln} \pi_{\theta}(\mathbf{a}_t\mid \mathbf{s}_t)\right]
$$

Contrary to before where we estimate the **Q-function** using the reward the principle of the **actor-critic** algorithm is to use a neural network $Q_{\theta^{'}}$ to approximate the **Q-function**.

So the algorithm will train two ANN one for the **actor** $\pi_{\theta}(\mathbf{a}\mid \mathbf{s})$ and one for the **critic** $Q_{\theta^{'}}(\mathbf{s},\mathbf{a})$. For the actor the principle will be the same:

- we will use a classifying Neural Network for $\pi_{\theta}(\mathbf{a}\mid \mathbf{s})$,
- the weights of the **sparse categorial entropy** are given by  $Q_{\theta^{'}}(\mathbf{s},\mathbf{a})$

For the **critic** we propose to make as with the **DQN** algorithm taking a **regression ANN** with the TD error to construct the reference value:

$$
\delta_t = \mathbf{r}_{r+1}+\gamma Q_{\theta^{'}}(\mathbf{s}_{t+1},\mathbf{a}_{t+1}) - Q_{\theta^{'}}(\mathbf{s}_{t},\mathbf{a}_{t})
$$

Since the next action $\mathbf{a}_{t+1}$ use to evaluate the policy (computation of the $Q$-function) we have a **on policy** algorithm since we use the same policy $\pi_{\theta_k}$ for exploration and evaluation. It is why we don't use experience replay.

**Algorithm (Actor-critic)**:
- Initialize $\theta$ arbitrarly
- Initialize $\theta^{'}$ arbitrarly
- for all the episodes $k$ 1 to $T$:
 - choose randomly a initial state $\mathbf{s}_0$
 - sample $\mathbf{a}_t$ with $\pi_{\theta_k}(\mathbf{a}\mid \mathbf{s})$
 - such that $\mathbf{s}_t$ is terminal:
     - compute $\mathbf{r}_{t+1}$ and $\mathbf{s}_{t+1}$ using $\mathbf{a}_t$
     - choose an action $\mathbf{a}_{t+1}$ using exploration policy $\pi_{\theta_k}(\mathbf{a}_t \mid \mathbf{s}_t)$
     
     - update the ANN respect to $\theta_k$ with a **spare-cross-entropy loss** with:
     
       - $\pi_{\theta_{k}}(\mathbf{a}\mid \mathbf{s})$ as predicted values,
       - list of index action as target values,
       - $Q_{\theta_k^{'}}(\mathbf{s},\mathbf{a})$ as sample weight of the loss.
     
     - compute the reference solution for the regression:
     
     $$
     \mathbf{y}_t = \left\{\begin{array}{l} \mathbf{r}_{t+1} \mbox{ if $\mathbf{s}_t$ is terminal}\\
     \mathbf{r}_{t+1} + \gamma Q_{\theta_k^{'}}(\mathbf{s}_{t+1},\mathbf{a}_{t+1}) \mbox{ else }
     \end{array}\right. 
     $$
     
     - update the ANN respect to $\theta_k^{'}$ with the loss:
      
     $$
     \mid \mathbf{y}_t - Q_{\theta_k^{'}}(\mathbf{s}_{t},\mathbf{a}_t) \mid^2
     $$
     
     - $\mathbf{a}_t := \mathbf{a}_{t+1}, \quad \mathbf{s}_t := \mathbf{s}_{t+1}$

**Algorithm (Actor-critic v2)**:
- Initialize $\theta$ arbitrarily
- Initialize $\theta^{'}$ arbitrarily
- for all the episodes $k$ 1 to $T$:
 - choose randomly a initial state $\mathbf{s}_0$
 - compute and store a trajectory $(\mathbf{s}_0,\mathbf{a}_0,\mathbf{r}_1,\mathbf{s}_1,...,\mathbf{r}_T)$  following $\pi_{\theta_k}(.\mid.)$
 - compute and store the reference solution fo the regression for a trajectory:
      
     $$
     \mathbf{y}_t = \left\{\begin{array}{l} \mathbf{r}_{t+1} \mbox{ if $\mathbf{s}_t$ is terminal}\\
     \mathbf{r}_{t+1} + \gamma Q_{\theta_k^{'}}(\mathbf{s}_{t+1},\mathbf{a}_{t+1}) \mbox{ else }
     \end{array}\right. 
     $$

     
 - update the ANN respect to $\theta_k$ with a **spare-cross-entropy loss** with:
     
     - $\pi_{\theta_{k}}(\mathbf{a}\mid \mathbf{s})$ as predicted values,
     - list of index action as target values,
     - $Q_{\theta_k^{'}}(\mathbf{s},\mathbf{a})$ as sample weight of the loss.
     
 
     
 - update the ANN respect to $\theta_k^{'}$ with the loss (for one data): $\mid \mathbf{y} - Q_{\theta_k^{'}}(\mathbf{s},\mathbf{a}) \mid^2$
